In [1]:
%cd VideoMAEv2

/home/exouser/VideoMAEv2


In [2]:
import torch
print(torch.cuda.is_available())
print(torch.cuda.get_device_name(0))

True
GRID A100X-40C


In [3]:
import os

current_dir = os.getcwd()
print("Current Directory:", current_dir)

Current Directory: /home/exouser/VideoMAEv2


In [4]:
import torch
from models.modeling_pretrain import pretrain_videomae_base_patch16_224

# If the function requires specific arguments, provide them here
model = pretrain_videomae_base_patch16_224()

# Count the number of parameters
total_params = sum(p.numel() for p in model.parameters())
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)

print(f"Total parameters: {total_params}")
print(f"Trainable parameters: {trainable_params}")

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")


Total parameters: 101307264
Trainable parameters: 101307264


In [5]:
# Save the model's state dictionary to a .pth file
torch.save(model.state_dict(), 'work_dir/pretrain_videomae_base_patch16_224_ucf/videomae_base_patch16_224_ucf_initial.pth')

In [9]:
import os
import shutil

# Paths
DATA_PATH = 'data/ucf101_1/train.csv'
NEW_PATH_DIR = 'data/ucf101_pretrain/'
NEW_PATH = os.path.join(NEW_PATH_DIR, 'train_pretrain.csv')

# Ensure the target directory exists
os.makedirs(NEW_PATH_DIR, exist_ok=True)

# Step 1: Make a copy
shutil.copy(DATA_PATH, NEW_PATH)

# Step 2: Process each line
with open(NEW_PATH, 'r') as f:
    lines = f.readlines()

# Modify the lines as per requirement
new_lines = [line.rsplit(' ', 1)[0] + " 0 -1\n" for line in lines]

# Step 3: Save back to the copied file
with open(NEW_PATH, 'w') as f:
    f.writelines(new_lines)

print(f"File saved to {NEW_PATH}")




File saved to data/ucf101_pretrain/train_pretrain.csv


In [10]:
# Define paths and any environment variables first
OUTPUT_DIR = 'work_dir/pretrain_videomae_base_patch16_224_ucf'
DATA_PATH = 'data/ucf101_pretrain/train_pretrain.csv'
# Only use the train ds for pretrain. valid and test is unseen for model.
import os
# --num_workers 24 
# Set environment variable
os.environ["OMP_NUM_THREADS"] = "1"

# Execute the python script with necessary parameters
!python -u run_mae_pretraining.py \
        --data_path {DATA_PATH} \
        --mask_type tube \
        --mask_ratio 0.9 \
        --decoder_mask_type run_cell \
        --decoder_mask_ratio 0.5 \
        --model pretrain_videomae_base_patch16_224 \
        --decoder_depth 4 \
        --batch_size 32 \
        --num_frames 16 \
        --sampling_rate 4 \
        --num_sample 2 \
        --num_workers 24 \
        --opt adamw \
        --lr 1e-3 \
        --clip_grad 0.02 \
        --opt_betas 0.9 0.95 \
        --warmup_epochs 20 \
        --save_ckpt_freq 20 \
        --epochs 200 \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR}

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(auto_resume=True, batch_size=32, clip_grad=0.02, color_jitter=0.0, data_path='data/ucf101_pretrain/train_pretrain.csv', data_root='', decoder_depth=4, decoder_mask_ratio=0.5, decoder_mask_type='run_cell', device='cuda', dist_on_itp=False, dist_url='env://', distributed=False, drop_path=0.0, epochs=200, finetune='', fname_tmpl='img_{:05}.jpg', imagenet_default_mean_and_std=True, input_size=224, local_rank=-1, log_dir='work_dir/pretrain_videomae_base_patch16_224_ucf', lr=0.001, mask_ratio=0.9, mask_type='tube', min_lr=1e-05, model='pretrain_videomae_base_patch16_224', momentum=0.9, normlize_target=True, num_frames=16, num_sample=2, num_workers=24, opt='adamw', opt_betas=[0.9, 0.95],

In [11]:
import json

# Path to the log file
log_file_path = "work_dir/pretrain_videomae_base_patch16_224_ucf/log.txt"

# Initialize minimum loss to a large value and line number to None
min_loss = float('inf')
min_loss_line_num = None

# Open the log file and process each line
with open(log_file_path, 'r') as log_file:
    for i, line in enumerate(log_file):
        # Check if the line number matches the given condition
        if i % 20 == 19 and i <= 200:
            data = json.loads(line)
            if 'train_loss' in data and data['train_loss'] < min_loss:
                min_loss = data['train_loss']
                min_loss_line_num = i

print(f"The smallest loss is {min_loss} at line number {min_loss_line_num + 1}.")


The smallest loss is 0.7252373578041558 at line number 200.


In [14]:
# Define paths and any environment variables first
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_b_ucf101_ucf101_{split_num}_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_base_patch16_224_ucf/checkpoint-199.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters (Adjust these as per your requirements)

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_base_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 8 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 50 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=8, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_b_ucf101_ucf101_1_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=50, eval=False, eval_data_path=None, finetune='/home/exouser/VideoMAEv2/work_dir

In [6]:
# Define paths and any environment variables first
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_b_ucf101_initial_ucf101_{split_num}_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_base_patch16_224_ucf/videomae_base_patch16_224_ucf_initial.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters All Initial

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_base_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 8 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 50 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=8, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_b_ucf101_initial_ucf101_1_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=50, eval=False, eval_data_path=None, finetune='/home/exouser/VideoMAEv2/

In [5]:
# hyperparameter


# Define paths and any environment variables first
OUTPUT_DIR = 'work_dir/pretrain_videomae_base_patch16_224_num_sample4'
DATA_PATH = 'train.csv'

import os
# --num_workers 24 
# Set environment variable
os.environ["OMP_NUM_THREADS"] = "1"

# Execute the python script with necessary parameters
!python -u run_mae_pretraining.py \
        --data_path {DATA_PATH} \
        --mask_type tube \
        --mask_ratio 0.9 \
        --with_checkpoint \
        --decoder_mask_type run_cell \
        --decoder_mask_ratio 0.5 \
        --model pretrain_videomae_base_patch16_224 \
        --decoder_depth 4 \
        --batch_size 16 \
        --num_frames 16 \
        --sampling_rate 4 \
        --num_sample 4 \
        --num_workers 24 \
        --opt adamw \
        --auto_resume \
        --lr 1e-3 \
        --clip_grad 0.02 \
        --opt_betas 0.9 0.95 \
        --warmup_epochs 20 \
        --save_ckpt_freq 20 \
        --epochs 200 \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR}

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(auto_resume=True, batch_size=16, clip_grad=0.02, color_jitter=0.0, data_path='train.csv', data_root='', decoder_depth=4, decoder_mask_ratio=0.5, decoder_mask_type='run_cell', device='cuda', dist_on_itp=False, dist_url='env://', distributed=False, drop_path=0.0, epochs=200, finetune='', fname_tmpl='img_{:05}.jpg', imagenet_default_mean_and_std=True, input_size=224, local_rank=-1, log_dir='work_dir/pretrain_videomae_base_patch16_224_num_sample4', lr=0.001, mask_ratio=0.9, mask_type='tube', min_lr=1e-05, model='pretrain_videomae_base_patch16_224', momentum=0.9, normlize_target=True, num_frames=16, num_sample=4, num_workers=24, opt='adamw', opt_betas=[0.9, 0.95], opt_eps=1e-08, output

In [6]:
# Define paths and any environment variables first
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_b_tiktok6000_numsample4_ucf101_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_base_patch16_224_num_sample4/checkpoint-199.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters (Adjust these as per your requirements)

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_base_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 8 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 50 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=8, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_b_tiktok6000_numsample4_ucf101_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=50, eval=False, eval_data_path=None, finetune='/home/exouser/VideoM

In [4]:
# Define paths and any environment variables first
OUTPUT_DIR = 'work_dir/pretrain_videomae_base_patch16_224'
DATA_PATH = 'train.csv'

import os
# --num_workers 24 
# Set environment variable
os.environ["OMP_NUM_THREADS"] = "1"

# Execute the python script with necessary parameters
!python -u run_mae_pretraining.py \
        --data_path {DATA_PATH} \
        --mask_type tube \
        --mask_ratio 0.9 \
        --decoder_mask_type run_cell \
        --decoder_mask_ratio 0.5 \
        --model pretrain_videomae_base_patch16_224 \
        --decoder_depth 4 \
        --batch_size 32 \
        --num_frames 16 \
        --sampling_rate 4 \
        --num_sample 2 \
        --auto_resume \
        --num_workers 24 \
        --opt adamw \
        --lr 1e-3 \
        --clip_grad 0.02 \
        --opt_betas 0.9 0.95 \
        --warmup_epochs 20 \
        --save_ckpt_freq 20 \
        --epochs 300 \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR}

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(auto_resume=True, batch_size=32, clip_grad=0.02, color_jitter=0.0, data_path='train.csv', data_root='', decoder_depth=4, decoder_mask_ratio=0.5, decoder_mask_type='run_cell', device='cuda', dist_on_itp=False, dist_url='env://', distributed=False, drop_path=0.0, epochs=300, finetune='', fname_tmpl='img_{:05}.jpg', imagenet_default_mean_and_std=True, input_size=224, local_rank=-1, log_dir='work_dir/pretrain_videomae_base_patch16_224', lr=0.001, mask_ratio=0.9, mask_type='tube', min_lr=1e-05, model='pretrain_videomae_base_patch16_224', momentum=0.9, normlize_target=True, num_frames=16, num_sample=2, num_workers=24, opt='adamw', opt_betas=[0.9, 0.95], opt_eps=1e-08, output_dir='work_d

In [5]:
# Define paths and any environment variables first
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_b_tiktok6000_ucf101_300epoch_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_base_patch16_224/checkpoint-259.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters (Adjust these as per your requirements)

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_base_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 8 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 50 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=8, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_b_tiktok6000_ucf101_300epoch_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=50, eval=False, eval_data_path=None, finetune='/home/exouser/VideoMAE

In [2]:
import os
import random

base_path = '/home/exouser/VideoMAEv2'
split_num = 1  # This can be changed to 2 or 3 if needed

OUTPUT_DIR = os.path.join(base_path, f'work_dir/vit_b_ucf101_ucf101_100epoch_{split_num}_ft')
DATA_PATH = os.path.join(base_path, f'data/ucf101_{split_num}')
MODEL_PATH = os.path.join(base_path, 'work_dir/pretrain_videomae_base_patch16_224_ucf/checkpoint-199.pth')
os.environ['CUDA_LAUNCH_BLOCKING'] = '1'
# Environment variables
os.environ["MASTER_PORT"] = str(12000 + random.randint(0, 20000))
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["DS_BUILD_OPS"] = "1"

# Parameters (Adjust these as per your requirements)

# Execute the python script with necessary parameters using -u for unbuffered output
!python -u run_class_finetuning.py \
        --model vit_base_patch16_224 \
        --data_set UCF101 \
        --nb_classes 101 \
        --data_path {DATA_PATH} \
        --finetune {MODEL_PATH} \
        --log_dir {OUTPUT_DIR} \
        --output_dir {OUTPUT_DIR} \
        --batch_size 8 \
        --num_sample 2 \
        --input_size 224 \
        --short_side_size 224 \
        --save_ckpt_freq 10 \
        --num_frames 16 \
        --sampling_rate 4 \
        --opt adamw \
        --lr 1e-3 \
        --layer_decay 0.90 \
        --num_workers 24 \
        --opt_betas 0.9 0.999 \
        --weight_decay 0.05 \
        --epochs 100 \
        --drop_path 0.35 \
        --head_drop_rate 0.5 \
        --test_num_segment 5 \
        --test_num_crop 3 \
        --dist_eval --enable_deepspeed

/home/exouser/miniconda3/envs/videomae/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libc10_hip.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
Not using distributed mode
Namespace(aa='rand-m7-n4-mstd0.5-inc1', attn_drop_rate=0.0, auto_resume=True, batch_size=8, clip_grad=None, color_jitter=0.4, crop_pct=None, cutmix=1.0, cutmix_minmax=None, data_path='/home/exouser/VideoMAEv2/data/ucf101_1', data_root='', data_set='UCF101', deepscale=False, deepscale_config=None, deepspeed=False, deepspeed_config='/home/exouser/VideoMAEv2/work_dir/vit_b_ucf101_ucf101_100epoch_1_ft/deepspeed_config.json', deepspeed_mpi=False, device='cuda', disable_eval_during_finetuning=False, dist_eval=True, dist_on_itp=False, dist_url='env://', distributed=False, drop=0.0, drop_path=0.35, enable_deepspeed=True, epochs=100, eval=False, eval_data_path=None, finetune='/home/exouser/VideoMAEv